# Bonito: Synthetic Data Generation

#### Environment Setup

In [18]:
import transformers
import torch
import vllm
import awq

torch.__version__, transformers.__version__, vllm.__version__, awq.__version__

('2.4.0+cu121', '4.44.2', '0.6.1.post2', '0.2.6')

#### Quantized Bonito Wrapper
This is a simplified quantized bonito class to generate a single synthetic input-output instruction for a given text and task type.
This code uses huggingface `transformers` library for generation.
For complete functionality and faster generations, we recommend using the `Bonito` class from the package.

In [13]:
from typing import Dict, Optional, Union
from datasets import Dataset

SHORTFORM_TO_FULL_TASK_TYPES = {
    "exqa": "extractive question answering",
    "mcqa": "multiple-choice question answering",
    "qg": "question generation",
    "qa": "question answering without choices",
    "ynqa": "yes-no question answering",
    "coref": "coreference resolution",
    "paraphrase": "paraphrase generation",
    "paraphrase_id": "paraphrase identification",
    "sent_comp": "sentence completion",
    "sentiment": "sentiment",
    "summarization": "summarization",
    "text_gen": "text generation",
    "topic_class": "topic classification",
    "wsd": "word sense disambiguation",
    "te": "textual entailment",
    "nli": "natural language inference",
}

class AbstractBonito:
    def _prepare_bonito_input(
        self, context_dataset: Dataset, task_type: str, context_col: str, **kwargs
    ) -> Dataset:
        """
        Prepares the input for the Bonito model.

        This method takes a context dataset, a task type, and a context
        column name, and prepares the dataset for the Bonito model.
        If the task type is not recognized, it raises a ValueError.

        Args:
            context_dataset (Dataset): The dataset that provides the
                context for the task.
            task_type (str): The type of the task. This can be a
                short form or a full form. If the task type is not
                recognized, a ValueError is raised.
            context_col (str): The name of the column in the dataset
                that provides the context for the task.
            **kwargs: Additional keyword arguments.

        Returns:
            Dataset: The prepared dataset for the Bonito model.
        """
        # get the task type name
        if task_type in SHORTFORM_TO_FULL_TASK_TYPES.values():
            full_task_type = task_type
        elif task_type in SHORTFORM_TO_FULL_TASK_TYPES:
            full_task_type = SHORTFORM_TO_FULL_TASK_TYPES[task_type]
        else:
            raise ValueError(f"Task type {task_type} not recognized")

        def process(example):
            input_text = "<|tasktype|>\n" + full_task_type.strip()
            input_text += (
                "\n<|context|>\n" + example[context_col].strip() + "\n<|task|>\n"
            )
            return {
                "input": input_text,
            }

        return context_dataset.map(
            process,
            remove_columns=context_dataset.column_names,
            num_proc=kwargs.get("num_proc", 1),
        )

    def _postprocess_dataset(
        self, synthetic_dataset: Dataset, context_col: str, **kwargs
    ) -> Dataset:
        """
        Post-processes the synthetic dataset.

        This method takes a synthetic dataset and a context column
        name, and post-processes the dataset. It filters out
        examples where the prediction does not contain exactly two
        parts separated by "<|pipe|>", and then maps each example to a
        new format where the context is inserted into the first part of
        the prediction and the second part of the prediction is used as
        the output.

        Args:
            synthetic_dataset (Dataset): The synthetic dataset to be
                post-processed.
            context_col (str): The name of the column in the dataset
                that provides the context for the tasks.
            **kwargs: Additional keyword arguments.

        Returns:
            Dataset: The post-processed synthetic dataset.
        """
        synthetic_dataset = synthetic_dataset.filter(
            lambda example: len(example["prediction"].split("<|pipe|>")) == 2
        )

        def process(example):
            pair = example["prediction"].split("<|pipe|>")
            context = example[context_col].strip()
            return {
                "input": pair[0].strip().replace("{{context}}", context),
                "output": pair[1].strip(),
            }

        synthetic_dataset = synthetic_dataset.map(
            process,
            remove_columns=synthetic_dataset.column_names,
            num_proc=kwargs.get("num_proc", 1),
        )

        return synthetic_dataset


In [4]:
from typing import Optional, List, Dict
from datasets import Dataset
from awq import AutoAWQForCausalLM
from transformers import AutoTokenizer

class AWQBonito(AbstractBonito):
    def __init__(self, model_name_or_path):
        self.model = AutoAWQForCausalLM.from_quantized(model_name_or_path, fuse_layers=True, torch_dtype=torch.float16)
        self.tokenizer = AutoTokenizer.from_pretrained(model_name_or_path, trust_remote_code=True)        
    
    def generate_task(
        self,
        unannotated_paragraph: str,
        task_type: str,
        sampling_params: dict,
        context_col="input"
    ) -> Dict:
        """
        Generates synthetic instruction tuning pair using the Quantized Bonito model.
        This method takes a text unannotated text, a task type, and sampling parameters,
        and generates synthetic input-output pair.

        Args:
            unannotated_paragraph (str): The unannotated text or a paragraph
            task_type (str): The type of the tasks. This can be a
                short form or a full form.
            sampling_params (dict): The parameters for
                sampling.
            **kwargs: Additional keyword arguments.

        Returns:
            Dict: The synthetic input-output pair for the task type.
        """

        text_dataset = Dataset.from_list([{context_col: unannotated_paragraph}])

        processed_dataset = self._prepare_bonito_input(
            text_dataset, task_type, context_col=context_col
        )

        outputs = self._generate_text(processed_dataset["input"], sampling_params)
        examples = []
        for i, example in enumerate(text_dataset.to_list()):
            output = outputs[i]
            example["prediction"] = output.strip()
            examples.append(example)

        synthetic_dataset = Dataset.from_list(examples)

        # filter out the examples that cannot be parsed
        synthetic_dataset_dict = self._postprocess_dataset(
            synthetic_dataset, context_col=context_col
        ).to_list()[0]

        return synthetic_dataset_dict

    def _generate_text(
        self,
        dataset: Dataset,
        sampling_params: dict,
    ) -> List[str]:
        """
        Generate text using huggingface transformers generate function.

        This method takes a dataset of prompts, encodes them,
        generates text using the model, decodes the generated
        text, and appends it to a list.

        Args:
            dataset (Dataset): A dataset containing prompts for text generation.
            sampling_params (dict): Parameters for sampling during generation.

        Returns:
            List[str]: A list of generated texts corresponding to the prompts.
        """
        generated_texts = []

        for prompt in dataset:
            input_ids = self.tokenizer.encode(prompt, return_tensors="pt")
            input_ids = input_ids.cuda()

            output = self.model.generate(input_ids, do_sample=True, **sampling_params)

            generated_text = self.tokenizer.decode(
                output[0][len(input_ids[0]) :], skip_special_tokens=True
            )
            generated_texts.append(generated_text)

        return generated_texts

In [5]:
from datasets import Dataset
from vllm import LLM, SamplingParams

class VLLMBonito(LLM, AbstractBonito):
    
    def generate_tasks(
        self,
        text_dataset: Dataset,
        context_col: str,
        task_type: str,
        sampling_params: SamplingParams,
        **kwargs,
    ):
        """
        Generates tasks using the Bonito model.

        This method takes a text dataset, a context column name,
        a task type, and sampling parameters, and generates tasks
        using the Bonito model. It processes the input dataset,
        generates outputs, collects multiple generations into
        one dataset object, and filters out the examples that
        cannot be parsed.

        Args:
            text_dataset (Dataset): The dataset that provides the text
                for the tasks.
            context_col (str): The name of the column in the dataset
                that provides the context for the tasks.
            task_type (str): The type of the tasks. This can be a
                short form or a full form.
            sampling_params (SamplingParams): The parameters for
                sampling.
            **kwargs: Additional keyword arguments.

        Returns:
            Dataset: The synthetic dataset with the generated tasks.
        """
        processed_dataset = self._prepare_bonito_input(
            text_dataset, task_type, context_col, **kwargs
        )
        outputs = self.generate(processed_dataset["input"], sampling_params)

        # collect multiple generations into one dataset object
        examples = []
        for i, example in enumerate(text_dataset.to_list()):
            for output in outputs[i].outputs:
                examples.append(
                    {"context": example[context_col], "prediction": output.text.strip()}
                )

        synthetic_dataset = Dataset.from_list(examples)

        # filter out the examples that cannot be parsed
        synthetic_dataset = self._postprocess_dataset(
            synthetic_dataset, context_col="context", **kwargs
        )

        return synthetic_dataset

## Synthetic Data Generation
Here we will load the quantized bonito model and generate synthetic instruction for the unannotated text.

```
SHORTFORM_TO_FULL_TASK_TYPES = {
    "exqa": "extractive question answering",
    "mcqa": "multiple-choice question answering",
    "qg": "question generation",
    "qa": "question answering without choices",
    "ynqa": "yes-no question answering",
    "coref": "coreference resolution",
    "paraphrase": "paraphrase generation",
    "paraphrase_id": "paraphrase identification",
    "sent_comp": "sentence completion",
    "sentiment": "sentiment",
    "summarization": "summarization",
    "text_gen": "text generation",
    "topic_class": "topic classification",
    "wsd": "word sense disambiguation",
    "te": "textual entailment",
    "nli": "natural language inference",
}
```

### Generate the synthetic instructions
After loading the model, we pass the unannotated paragraph and the task type to generate the instructions.
Here we generate an NLI task:

In [11]:
## sample text
unannotated_paragraph = """
1. “Confidential Information”, whenever used in this Agreement, shall mean any data, document, specification and other information or material, that is delivered or disclosed by UNHCR to the Recipient in any form whatsoever, whether orally, visually in writing or otherwise (including computerized form), and that, at the time of disclosure to the Recipient, is designated as confidential.
"""
unannotated_paragraph

'\n1. “Confidential Information”, whenever used in this Agreement, shall mean any data, document, specification and other information or material, that is delivered or disclosed by UNHCR to the Recipient in any form whatsoever, whether orally, visually in writing or otherwise (including computerized form), and that, at the time of disclosure to the Recipient, is designated as confidential.\n'

### Quantized Bonito : AWQ Inference

In [ ]:
import torch

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model_id = 'mychen76/Llama-3.1-8B-bonito-v1-awq'
bonito = AWQBonito(model_id)

### generate nli

In [ ]:
from transformers import set_seed
from pprint import pprint
set_seed(2)

# Generate synthetic instruction tuning dataset
sampling_params = {
    "max_new_tokens": 256,
    "top_p": 0.95,
    "temperature": 0.7,
    "num_return_sequences": 1,
}
synthetic_dataset = bonito.generate_task(
    unannotated_paragraph, task_type="nli", sampling_params=sampling_params
)
pprint("----Generated Instructions----")
pprint(f'Input: {synthetic_dataset["input"]}')
pprint(f'Output: {synthetic_dataset["output"]}')

### generate qa

In [ ]:
from transformers import set_seed
from pprint import pprint
set_seed(2)

# Generate synthetic instruction tuning dataset
sampling_params = {
    "max_new_tokens": 256,
    "top_p": 0.95,
    "temperature": 0.7,
    "num_return_sequences": 1,
}
synthetic_dataset = bonito.generate_task(
    unannotated_paragraph, task_type="qa", sampling_params=sampling_params
)
pprint("----Generated Instructions----")
pprint(f'Input: {synthetic_dataset["input"]}')
pprint(f'Output: {synthetic_dataset["output"]}')

### vLLM Bonito : AWQ Inference
ValueError: The model's max seq len (131072) is larger than the maximum number of tokens that can be stored in KV cache (129248). Try increasing `gpu_memory_utilization` or decreasing `max_model_len` when initializing the engine.

In [1]:
from datasets import load_dataset

# load dataaset with unannotated text
unannotated_text_ds = load_dataset(
    "BatsResearch/bonito-experiment",
    "unannotated_contract_nli"
)["train"].select(range(10))

In [6]:
from vllm import LLM, SamplingParams
import torch 

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model_id = 'mychen76/Llama-3.1-8B-bonito-v1-awq'

# Create an LLM.
vbonito = VLLMBonito(model=model_id, 
              quantization="AWQ",
              gpu_memory_utilization=0.80,
              max_seq_len_to_capture=4096,
              max_model_len=4096,
              speculative_max_model_len = 4096)


INFO 09-17 04:19:22 awq_marlin.py:93] Detected that the model can run with awq_marlin, however you specified quantization=awq explicitly, so forcing awq. Use quantization=awq_marlin for faster inference
WARNING 09-17 04:19:22 config.py:338] awq quantization is not fully optimized yet. The speed can be slower than non-quantized models.
INFO 09-17 04:19:22 llm_engine.py:223] Initializing an LLM engine (v0.6.1.post2) with config: model='mychen76/Llama-3.1-8B-bonito-v1-awq', speculative_config=None, tokenizer='mychen76/Llama-3.1-8B-bonito-v1-awq', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, override_neuron_config=None, rope_scaling=None, rope_theta=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.float16, max_seq_len=4096, download_dir=None, load_format=LoadFormat.AUTO, tensor_parallel_size=1, pipeline_parallel_size=1, disable_custom_all_reduce=False, quantization=awq, enforce_eager=False, kv_cache_dtype=auto, quantization_param_path=None, device_confi

Loading safetensors checkpoint shards:   0% Completed | 0/2 [00:00<?, ?it/s]


INFO 09-17 04:19:24 model_runner.py:1008] Loading model weights took 5.3745 GB
INFO 09-17 04:19:26 gpu_executor.py:122] # GPU blocks: 6132, # CPU blocks: 2048
INFO 09-17 04:19:28 model_runner.py:1311] Capturing the model for CUDA graphs. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI.
INFO 09-17 04:19:28 model_runner.py:1315] CUDA graphs can take additional 1~3 GiB memory per GPU. If you are running out of memory, consider decreasing `gpu_memory_utilization` or enforcing eager mode. You can also reduce the `max_num_seqs` as needed to decrease memory usage.
INFO 09-17 04:19:39 model_runner.py:1430] Graph capturing finished in 11 secs.


#### generate "nli": "natural language inference"

In [8]:
from vllm import SamplingParams
from transformers import set_seed
from pprint import pprint
set_seed(2)

# Generate synthetic instruction tuning dataset
sampling_params = SamplingParams(max_tokens=256, top_p=0.95, temperature=0.5, n=1)

synthetic_dataset = vbonito.generate_tasks(
    unannotated_text_ds,
    context_col="input",
    task_type="nli",
    sampling_params=sampling_params
)

pprint("----Generated Instructions----")
pprint(f'Input: {synthetic_dataset["input"]}')
pprint(f'Output: {synthetic_dataset["output"]}')

Processed prompts: 100%|██████████████████| 10/10 [00:01<00:00,  7.72it/s, est. speed input: 757.82 toks/s, output: 359.21 toks/s]


Filter:   0%|          | 0/10 [00:00<?, ? examples/s]

Map:   0%|          | 0/10 [00:00<?, ? examples/s]

'----Generated Instructions----'
("Input: ['Given that 2.3 Provided that the Recipient has a written agreement "
 'with the following persons or entities requiring them to treat the '
 'Confidential Information in accordance with this Agreement, the Recipient '
 'may disclose the Confidential Information to: 2.3.1  Any other party with '
 'the Discloser’s prior written consent; and 2.3.2 the Recipient’s employees, '
 'officials, representatives and agents who have a strict need to know the '
 'contents of the Confidential Information, and employees, officials, '
 'representatives and agents of any legal entity that it controls, controls '
 'it, or with which it is under common control, who have a similar need to '
 'know the contents of the Confidential Information, provided that, for these '
 'purposes a controlled legal entity means: Does it follow that The Recipient '
 "is a person Yes, no, or maybe?', '5. All Confidential Information in any "
 'form and any medium, including all co

#### "exqa": "extractive question answering",

In [12]:
from vllm import SamplingParams
from transformers import set_seed
from pprint import pprint
set_seed(2)

# Generate synthetic instruction tuning dataset
sampling_params = SamplingParams(max_tokens=256, top_p=0.95, temperature=0.5, n=1)

synthetic_dataset = vbonito.generate_tasks(
    unannotated_text_ds,
    context_col="input",
    task_type="exqa",
    sampling_params=sampling_params
)

pprint("----Generated Instructions----")
pprint(f'Input: {synthetic_dataset["input"]}')
pprint(f'Output: {synthetic_dataset["output"]}')

Map:   0%|          | 0/10 [00:00<?, ? examples/s]

Processed prompts: 100%|█████████████████| 10/10 [00:00<00:00, 10.39it/s, est. speed input: 1030.27 toks/s, output: 429.36 toks/s]


Filter:   0%|          | 0/10 [00:00<?, ? examples/s]

Map:   0%|          | 0/10 [00:00<?, ? examples/s]

'----Generated Instructions----'
('Input: [\'Given the following passage\\n\\n"2.3 Provided that the Recipient '
 'has a written agreement with the following persons or entities requiring '
 'them to treat the Confidential Information in accordance with this '
 'Agreement, the Recipient may disclose the Confidential Information to: '
 '2.3.1  Any other party with the Discloser’s prior written consent; and 2.3.2 '
 'the Recipient’s employees, officials, representatives and agents who have a '
 'strict need to know the contents of the Confidential Information, and '
 'employees, officials, representatives and agents of any legal entity that it '
 'controls, controls it, or with which it is under common control, who have a '
 'similar need to know the contents of the Confidential Information, provided '
 'that, for these purposes a controlled legal entity means:",\\n\\nanswer the '
 'following question: What is the third requirement for the Recipient to '
 "disclose the Confidential Infor